In [26]:
import os

dir_path = 'training_data\weather_data'
weather_list = []
for file_name in os.listdir(dir_path):
    
    if not file_name.startswith('._'):
        
        with open(os.path.join(dir_path, file_name), 'r') as f:            
            for line in f:
                
                parts = line.split()
                timestamp = parts[0] + ' ' + parts[1]
                sensor_id = parts[2]
                sensor_value = parts[3]
                station_id = parts[4]
                
                output = f"{timestamp}{sensor_id}{sensor_value}{station_id}"
                
                weather_list.append([timestamp, sensor_id, sensor_value, station_id])


dir_path = 'training_data\cluster_map'
file_name = 'cluster_map'
cluster_list = []

with open(os.path.join(dir_path, file_name), 'r') as f:
    
    for line in f:
        
        parts = line.split()
        regoin_hash = parts[0]
        regoin_id = parts[1]
        cluster_list.append([regoin_hash, regoin_id])


dir_path = 'training_data\order_data'
file_name = 'order_data_2016-01-03'
order_list = []
gap = 0
demand = 0
ease_time = ''
# for file_name in os.listdir(dir_path ):
#     if not file_name.startswith('._'):
with open(dir_path+"\\"+file_name, 'r') as f:
    for line in f:
        parts = line.split()
        order_id = parts[0]
        driver_id = parts[1]
        if driver_id == 'NULL':
            gap += 1
        passenger_id = parts[2]
        start_location = parts[3]
        start_location_id , end_location_id = '',''
        end_location = parts[4]
        for i in range(len(cluster_list)):
            if start_location == cluster_list[i][0]:
                start_location_id = cluster_list[i][1]
            if end_location == cluster_list[i][0]:
                end_location_id = cluster_list[i][1]
        price = parts[5]
        timestamp = parts[6] + ' ' + parts[7]
        #round off time to 5 minutes
        ease_time = timestamp[11:16]
        if int(ease_time[3:5]) % 5 != 0 and int(ease_time[3:5]) >5:
            ease_time = ease_time[0:3] + str(int(ease_time[3:5]) - int(ease_time[3:5]) % 5)
        elif int(ease_time[3:5]) % 5 != 0 and int(ease_time[3:5]) <5:
            ease_time = ease_time[0:3] + str(int(ease_time[3:5]) + int(ease_time[3:5]) % 5)
        
    
        for i in range(len(weather_list)):
            if ease_time == weather_list[i][0][11:16]:
                order_list.append([order_id, driver_id, start_location_id, end_location_id, price, timestamp, weather_list[i][1], weather_list[i][2]])
                break;
            
        demand += 1


# open the file in write mode
with open('reduced_order_list.txt_3', 'w') as f:
    # write the list to the file
    f.write("order_id,driver_id,start_location_id, end_location_id, price, timestamp, weather, temperature\n")
    for item in order_list:
        for i in item:
            # dont append comma after temperature
            if i == item[-1]:
                f.write("%s" % i)
            else:
                f.write("%s," % i)
        f.write("\n")


In [3]:

order_list = []
with open('reduced_order.txt', 'r') as f:
    lines = f.readlines()
    lines = lines[1:]
    for line in lines:
        parts = line.split(",")
        order_id = parts[0]
        driver_id = parts[1]
        start_location_id = parts[2]
        end_location_id = parts[3]
        price = parts[4]
        timestamp = parts[5]
        weather = parts[6]
        temperature = parts[7]
        order_list.append([order_id, driver_id, start_location_id, end_location_id, price, timestamp, weather, temperature])


In [27]:
import math

count = 0
count_list = []
start = '00:00'
end = '00:10'
interval = 0
unfilled_order = []
unfilled_order_wrt_time = []
region_sort = [[] for i in range(144)]
time = []
while interval < 144:
    for i in order_list:
        if i[1] == 'NULL' and i[5][11:16] >= start and i[5][11:16] < end :
            count +=1
            unfilled_order.append(i)
  
    count_list.append([start, end, count])
    time.append([start, end])
    unfilled_order_wrt_time.append(unfilled_order)
    unfilled_order = []
    count = 0
    start = end
    if int(end[3:5])+ 10 >= 60:
        if int(end[0:2]) + 1 < 10:
            end = '0' + str(int(end[0:2]) + 1) + ':' + '00'
        else:
            end = str(int(end[0:2]) + 1) + ':' + '00'
    else:
        end = end[0:3] + str(int(end[3:5]) + 10)

    # print(start, end)
    interval += 1

avg_price = 0
avg_weather = 0
avg_temperature = 0
count_list = []
count = 0
counter = 0
seen_values = set()  # keep track of unique values seen so far
for timesam in unfilled_order_wrt_time:
    for order in timesam:
        for order2 in timesam:
            if order[2] == order2[2]:
                count += 1
                avg_price = float(order[4]) + float(order2[4])/2
                avg_weather =  (float(order[6]) + float(order2[6]))/2
                avg_temperature = (float(order[7]) + float(order2[7]))/2
        key = (time[counter][0], time[counter][1], order[2])  # create a tuple key
        if key not in seen_values:  # add only if the key is new
            count_list.append([time[counter][0], time[counter][1],count, order[2],avg_price,math.floor(avg_weather),avg_temperature])
            seen_values.add(key)  # add the key to the set
        count = 0
    counter += 1


# with open('unfilled_order_list_wrt_time_2.txt', 'w') as f:
#     # write the list to the file
#     for item in unfilled_order_wrt_time:
#         f.write("%s\n" % item)


with open('model_data_3.txt','w') as f:
    f.write("start_time, end_time, gap, start_location_id, price, weather, temperature\n")
    for item in count_list:
        for j in item:
            if j == item[-1]:
                f.write("%s" %j)
            else:
                f.write("%s," %j)
        f.write("\n")

In [23]:

# plot gap and timeslot
import pandas as pd
import numpy as np

# Read in the data
df = pd.read_csv("model_data.txt")
gap = df.iloc[:, 2].values
start_time = df.iloc[:,0]
start_time

# plot gap and start_time
import matplotlib.pyplot as plt
plt.plot(start_time, gap)   
plt.xlabel('start_time')
plt.ylabel('gap')
plt.title('gap vs start_time')
plt.show()




0       00:00
1       00:00
2       00:00
3       00:00
4       00:00
        ...  
4424    23:50
4425    23:50
4426    23:50
4427    23:50
4428    23:50
Name: start_time, Length: 4429, dtype: object

In [29]:
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.linear_model import HuberRegressor
import pandas as pd
import numpy as np

# Read in the data
data = pd.read_csv("model_data.txt")
data = data.fillna(0.0)


# Extract predictor and response variables
X = data.iloc[:, 3:7].values

# Print X 
#print(X)

y = data.iloc[:, 2].values
#replace all nan with null
# import matplotlib.pyplot as plt

# Set the window size
window_size = 200

# Initialize lists to store the model performance metrics
r_squared_list = []
mse_list = []

# Loop through the data in overlapping windows
for i in range(len(y) - window_size + 1):
    
    # Extract the data for this window
    X_window = X[i:i+window_size-1,:]
    y_window = y[i:i+window_size-1]
    
    # Robust linear regression
    #model = HuberRegressor().fit(X_window, y_window)
    
    # Fit the linear regression model
    model = LinearRegression().fit(X_window, y_window)
    
    # Fit the decision tree model with max_depth=5
    #model = DecisionTreeRegressor(max_depth=5).fit(X_window, y_window)
    
    # Use the model to make predictions on the data in the window
    y_pred = model.predict(X_window)
    # Evaluate the model performance
    r_squared = model.score(X_window, y_window)
    
    #------------------------------------------------------
    # MSE 


    #-------------------------------------------------------
    
    mse = np.mean((y_window - y_pred)**2)
    
    # Append the metrics to the lists
    r_squared_list.append(r_squared)
    mse_list.append(mse)
    
    # Print the summary of the fitted model
    print("Window:", i+1)
    
    print("Regression Summary:\n", "Intercept:", model.intercept_, "\nCoefficients:", model.coef_, "\nR-squared:", r_squared)
    print("Second Predictor Variable:", X_window[:,1])
    print("Regression Coefficients:", model.coef_)
    print("Mean Squared Error:", mse)
    
# n = 66
# q = 144

# sum_inner = 0
# for i2 in range(1,n):
#     sum_t = 0
# for j in range(q):
    
#     for k in count_list:
#         if k[0] == time[j][0] and int(k[3]) == i2:
#             sum_t += k[2] - y_pred

# sum_inner += ((1/q) * sum_t)
# mse = abs((1/n) * sum_inner)


# Plot the model learning and error
# plt.plot(r_squared_list)
# plt.title("Model Learning")
# plt.xlabel("Window Number")
# plt.ylabel("R-squared")
# plt.show()

# plt.plot(mse_list)
# plt.title("Model Error")
# plt.xlabel("Window Number")
# plt.ylabel("Mean Squared Error")
# plt.show()

Window: 1
Regression Summary:
 Intercept: -94.62476973051989 
Coefficients: [ 3.04137039e-01 -3.90599993e-02  1.12797660e+02 -5.95126500e+00] 
R-squared: 0.7284150941893099
Second Predictor Variable: [ 49.5   18.5  114.     6.     9.   124.5   64.5   91.5   12.    13.5
  40.5    9.    10.5   13.     1.    28.    36.     1.   155.    13.5
   1.    57.5   14.5   24.     9.    13.     9.    37.5   13.5   17.5
  13.5   12.    67.    16.5   15.    21.    10.5   29.     9.5   22.
  10.     1.    17.    27.5   49.5   18.5   35.    14.     1.     1.
  17.5    1.    25.5    1.    34.5   40.    61.5    9.5   37.5   17.
   3.01   9.5   33.    58.5   14.5   46.5   84.    12.   180.     1.
  16.5   35.5    5.    37.     4.5   43.    31.5   57.5   14.     1.
  50.    17.5    1.    18.    49.5    1.    30.    58.    66.5  139.5
  18.5   21.    27.5  141.     1.    22.5   69.    28.    57.    16.5
  20.    33.   102.    30.    31.    10.5   24.    34.5    1.    31.5
   1.    19.    34.     1.    31.5 

In [35]:
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.linear_model import HuberRegressor
import pandas as pd
import numpy as np

# Read in the data
data = pd.read_csv("model_data.txt")
data = data.fillna(0.0)


# Extract predictor and response variables
X = data.iloc[:, 3:7].values

# Print X 
#print(X)

y = data.iloc[:, 2].values
#replace all nan with null
# import matplotlib.pyplot as plt

# Set the window size
window_size = 200

# Initialize lists to store the model performance metrics
r_squared_list = []
mse_list = []

# Loop through the data in overlapping windows
for i in range(len(y) - window_size + 1):
    
    # Extract the data for this window
    X_window = X[i:i+window_size-1,:]
    y_window = y[i:i+window_size-1]
    
    # Robust linear regression
    #model = HuberRegressor().fit(X_window, y_window)
    
    # Fit the linear regression model
    #model = LinearRegression().fit(X_window, y_window)
    
    # Fit the decision tree model with max_depth=5
    model = DecisionTreeRegressor(max_depth=5).fit(X_window, y_window)
    
    # Use the model to make predictions on the data in the window
    y_pred = model.predict(X_window)
    # Evaluate the model performance
    r_squared = model.score(X_window, y_window)
    
    
    mse = np.mean((y_window - y_pred)**2)
    
    # Append the metrics to the lists
    r_squared_list.append(r_squared)
    mse_list.append(mse)
    
    # Print the summary of the fitted model
    print("Window:", i+1)

    print("Mean Squared Error:", mse)
    
# n = 66
# q = 144

# sum_inner = 0
# for i2 in range(1,n):
#     sum_t = 0
# for j in range(q):
    
#     for k in count_list:
#         if k[0] == time[j][0] and int(k[3]) == i2:
#             sum_t += k[2] - y_pred

# sum_inner += ((1/q) * sum_t)
# mse = abs((1/n) * sum_inner)


# Plot the model learning and error
# plt.plot(r_squared_list)
# plt.title("Model Learning")
# plt.xlabel("Window Number")
# plt.ylabel("R-squared")
# plt.show()

# plt.plot(mse_list)
# plt.title("Model Error")
# plt.xlabel("Window Number")
# plt.ylabel("Mean Squared Error")
# plt.show()

Window: 1
Mean Squared Error: 415.546446403812
Window: 2
Mean Squared Error: 409.10800104418195
Window: 3
Mean Squared Error: 409.1042786651236
Window: 4
Mean Squared Error: 409.13731073096454
Window: 5
Mean Squared Error: 409.09659494738946
Window: 6
Mean Squared Error: 408.99741779716646
Window: 7
Mean Squared Error: 408.96139589230694
Window: 8
Mean Squared Error: 409.8906054821912
Window: 9
Mean Squared Error: 411.6789742362607
Window: 10
Mean Squared Error: 411.6816214702159
Window: 11
Mean Squared Error: 411.64300244918473
Window: 12
Mean Squared Error: 411.7335262169433
Window: 13
Mean Squared Error: 412.1971353312638
Window: 14
Mean Squared Error: 411.82442434041184
Window: 15
Mean Squared Error: 411.7883937132038
Window: 16
Mean Squared Error: 409.60207101785585
Window: 17
Mean Squared Error: 405.47208776827455
Window: 18
Mean Squared Error: 404.114105479251
Window: 19
Mean Squared Error: 556.8035945914787
Window: 20
Mean Squared Error: 557.1859669797358
Window: 21
Mean Square

In [47]:
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.linear_model import HuberRegressor
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

# Read in the data
data = pd.read_csv("model_data.txt")
data = data.fillna(0.0)


# Extract predictor and response variables
X = data.iloc[:, 3:7].values

# Print X 
#print(X)

y = data.iloc[:, 2].values
#replace all nan with null
# import matplotlib.pyplot as plt

# Set the window size
window_size = 200

# Initialize lists to store the model performance metrics
r_squared_list = []
mse_list = []

# Loop through the data in overlapping windows
for i in range(len(y) - window_size + 1):
    
    # Extract the data for this window
    X_window = X[i:i+window_size-1,:]
    y_window = y[i:i+window_size-1]
    
    # Robust linear regression
    #model = HuberRegressor().fit(X_window, y_window)
    
    # Fit the linear regression model
    model = LinearRegression().fit(X_window, y_window)
    
    # Fit the decision tree model with max_depth=5
    #model = DecisionTreeRegressor(max_depth=5).fit(X_window, y_window)
    
    # Random Forest
    model = RandomForestRegressor(n_estimators=100, max_depth=5, random_state=42).fit(X_window, y_window)
    
    # Use the model to make predictions on the data in the window
    y_pred = model.predict(X_window)
    # Evaluate the model performance
    r_squared = model.score(X_window, y_window)
    
    mse = np.mean((y_window - y_pred)**2)
    
    #------------------------------------------------------
    # MSE 
    
    # n = 66
    # q = 144

    # sum_inner = 0
    # for i2 in range(1,n):
    #     sum_t = 0
    # for j in range(q):
        
    #     for k in count_list:
    #         if k[0] == time[j][0] and int(k[3]) == i2:
    #             sum_t += k[2] - y_pred

    # sum_inner += ((1/q) * sum_t)
    # mse = abs((1/n) * sum_inner)

    #-------------------------------------------------------
    
    # Append the metrics to the lists
    r_squared_list.append(r_squared)
    mse_list.append(mse)
    
    # Print the summary of the fitted model
    print("Window:", i+1)
    
    # print("Regression Summary:\n", "Intercept:", model.intercept_, "\nCoefficients:", model.coef_, "\nR-squared:", r_squared)
    # #print("Second Predictor Variable:", X_window[:,1])
    # print("Regression Coefficients:", model.coef_)
    print("Mean Squared Error:", mse)

# Plot the model learning and error
# plt.plot(r_squared_list)
# plt.title("Model Learning")
# plt.xlabel("Window Number")
# plt.ylabel("R-squared")
# plt.show()

# plt.plot(mse_list)
# plt.title("Model Error")
# plt.xlabel("Window Number")
# plt.ylabel("Mean Squared Error")
# plt.show()

Window: 1
Mean Squared Error: 338.7174033453898
Window: 2
Mean Squared Error: 319.6049163563916
Window: 3
Mean Squared Error: 294.07185556249834
Window: 4
Mean Squared Error: 324.77161371260996
Window: 5
Mean Squared Error: 264.05503280056337
Window: 6
Mean Squared Error: 297.5744355848887
Window: 7
Mean Squared Error: 330.56615748803233
Window: 8
Mean Squared Error: 324.17770153715367
Window: 9
Mean Squared Error: 289.8764094559925
Window: 10
Mean Squared Error: 342.8428339264187
Window: 11
Mean Squared Error: 332.75612054478705
Window: 12
Mean Squared Error: 298.07411656023817
Window: 13
Mean Squared Error: 333.20855285475096
Window: 14
Mean Squared Error: 287.3457887318001
Window: 15
Mean Squared Error: 325.1584800812115
Window: 16
Mean Squared Error: 341.14873554535455
Window: 17
Mean Squared Error: 346.64269688429306
Window: 18
Mean Squared Error: 295.0338801431049
Window: 19
Mean Squared Error: 363.1415685276973
Window: 20
Mean Squared Error: 370.37470609925117
Window: 21
Mean Sq

KeyboardInterrupt: 

In [45]:
from sklearn.metrics import r2_score

data = pd.read_csv("model_data_3.txt")
data.head()
data = data.fillna(0.0)
X = data.iloc[:, 3:7].values
y = data.iloc[:, 2].values
y_pred = model.predict(X)
print(y_pred)
print(abs(r2_score(y, y_pred)))


[828.         828.         828.         ...   3.08333333   7.55882353
   2.7       ]
4.920929733651196
